In [ ]:
import numpy as np
import random
from scipy.stats import norm

# we create two sample data sets
#
# one where there is a genuine correlation, affected by fluctuations
#
# another where there is in reality only noise
#
def fct_a(x):
    return x*x*x - 10*x*x + 1000*x

def fct_b(x):
    return 10000

# x is a list of numbers
# a list of function values y is returned, affected by fluctuations both in x and y
#
def noisy_function(fct, x, std_dev_x, std_dev_y):
    x_with_noise = [norm.rvs(loc=el, scale=std_dev_x) for el in x]
    y_without_noise = [fct(el) for el in x_with_noise]
    y = [norm.rvs(loc=el, scale=std_dev_y) for el in y_without_noise]
    return y

In [ ]:
# training data sets (17 points)
#
x_dataset   = np.arange(6.8, 13.4, 0.4) 
y_dataset_a = noisy_function(fct_a, x_dataset, 2, 2000)
y_dataset_b = noisy_function(fct_b, x_dataset, 2, 2000)
print("*** TRAINING DATA ***\n\nx_dataset:\t", x_dataset)
print("y_dataset_a:\t", y_dataset_a)
print("y_dataset_b:\t", y_dataset_b)

# averages of training data for null hypothesis
#
y_dataset_average_a = sum(y_dataset_a) / len(y_dataset_a)
y_dataset_average_b = sum(y_dataset_b) / len(y_dataset_b)
print("Average of a): \t", y_dataset_average_a)
print("Average of b): \t", y_dataset_average_b)

In [ ]:
import seaborn as sbn
import matplotlib.pyplot as plt

fig, ax = plt.subplots()
fig.set_size_inches(13, 8)
plt.xticks(fontsize=18, color="#322300")
plt.yticks(fontsize=18, color="#322300")
ax.set_xlabel("x", fontsize=24, color="#322300")
ax.set_ylabel("y", fontsize=24, color="#322300")

sbn.scatterplot(x=x_dataset, y=y_dataset_a, color="#e6503c", s=70)  # red for data set A
sbn.scatterplot(x=x_dataset, y=y_dataset_b, color="#147864", s=70)  # green for data set B

sbn.lineplot(x=[6.8, 13.4], y=[y_dataset_average_b, y_dataset_average_b], color='#147864', ax=ax)
sbn.lineplot(x=[6.8, 13.4], y=[y_dataset_average_a, y_dataset_average_a], color='#e6503c', ax=ax)

ax.set(xlim=(6, 14))
ax.set(ylim=(0, 20000))

In [ ]:
# graphical linear regression using seaborn
#
fig, ax = plt.subplots()
fig.set_size_inches(13, 8)
plt.xticks(fontsize=18, color="#322300")
plt.yticks(fontsize=18, color="#322300")
ax.set_xlabel("x", fontsize=24, color="#322300")
ax.set_ylabel("y", fontsize=24, color="#322300")

sbn.regplot(x=x_dataset, y=y_dataset_a, color='#e6503c', order=1, \
            scatter_kws={'s':50}, ci=None, truncate=False)
sbn.regplot(x=x_dataset, y=y_dataset_b, color='#147864', order=1, \
            scatter_kws={'s':50}, ci=None, truncate=False)

ax.set(xlim=(6, 14))
ax.set(ylim=(0, 20000))

In [ ]:
# linear regression using statsmodels
#
import numpy as np
import statsmodels.api as sm

x_array = sm.add_constant(np.asarray(x_dataset))
linear_fit_a = sm.OLS(np.asarray(y_dataset_a), x_array).fit()
linear_fit_b = sm.OLS(np.asarray(y_dataset_b), x_array).fit()

print("Fit a):\n", linear_fit_a.summary())
print("Fit a) params:", linear_fit_a.params, end="\n\n")
print("Fit b):\n", linear_fit_b.summary())
print("Fit b) params:", linear_fit_b.params, end="\n\n")

In [ ]:
# graphical bilogarithmic regression using seaborn
#
import math

fig, ax = plt.subplots()
fig.set_size_inches(13, 8)
plt.xticks(fontsize=18, color="#322300")
plt.yticks(fontsize=18, color="#322300")
ax.set_xlabel("ln x", fontsize=24, color="#322300")
ax.set_ylabel("ln y", fontsize=24, color="#322300")

sbn.regplot(x=[math.log(el) for el in x_dataset], y=[math.log(el) for el in y_dataset_a], \
            color='#e6503c', order=1, scatter_kws={'s':50}, ci=None, truncate=False)
sbn.regplot(x=[math.log(el) for el in x_dataset], y=[math.log(el) for el in y_dataset_b], \
            color='#147864', order=1, scatter_kws={'s':50}, ci=None, truncate=False)

ax.set(xlim=(math.log(min(x_dataset)), math.log(max(x_dataset))))
ax.set(ylim=(math.log(min(min(y_dataset_a), min(y_dataset_b))), math.log(max(max(y_dataset_a), max(y_dataset_b)))))

In [ ]:
# bilogarithmic regression using statsmodels
#
import math

logx_array = sm.add_constant(np.asarray([math.log(el) for el in x_dataset]))
log_fit_a = sm.OLS(np.asarray([math.log(el) for el in y_dataset_a]), logx_array).fit()
log_fit_b = sm.OLS(np.asarray([math.log(el) for el in y_dataset_b]), logx_array).fit()

print("Fit a):\n", log_fit_a.summary())
print("Fit a) params:", log_fit_a.params, end="\n\n")
print("\nFit b):\n", log_fit_b.summary())
print("Fit b) params:", log_fit_b.params, end="\n\n")

In [ ]:
# third-order polynomial regression using statsmodels
#
x_expansion_2d_array = np.asarray([[1, x, x*x, x*x*x] for x in x_dataset])

cubic_fit_a = sm.OLS(np.asarray(y_dataset_a), x_expansion_2d_array).fit()
cubic_fit_b = sm.OLS(np.asarray(y_dataset_b), x_expansion_2d_array).fit()

print("Matrix of 1, x, x^2, x^3 values:\n", x_expansion_2d_array)
print("\nFit a):\n", cubic_fit_a.summary())
print("Fit a) params:", cubic_fit_a.params, end="\n\n")
print("\nFit b):\n", cubic_fit_b.summary())
print("Fit b) params:", cubic_fit_b.params, end="\n\n")

In [ ]:
# third-order polynomial regression using seaborn
#
fig, ax = plt.subplots()
fig.set_size_inches(13, 8)
plt.xticks(fontsize=18, color="#322300")
plt.yticks(fontsize=18, color="#322300")
ax.set_xlabel("x", fontsize=24, color="#322300")
ax.set_ylabel("y", fontsize=24, color="#322300")

sbn.regplot(x=x_dataset, y=y_dataset_a, color='#e6503c', order=3, \
            scatter_kws={'s':50}, ci=None, truncate=False)
sbn.regplot(x=x_dataset, y=y_dataset_b, color='#147864', order=3, \
            scatter_kws={'s':50}, ci=None, truncate=False)

# this is to verify that seaborn and statsmodels actually produce the same third-order correlation
#
sbn.lineplot(x=np.arange(7.8, 12.4, 0.2), y=[cubic_fit_a.params[3]*x*x*x + cubic_fit_a.params[2]*x*x + cubic_fit_a.params[1]*x + cubic_fit_a.params[0] for x in np.arange(7.8, 12.4, 0.2)], color='#322300', ax=ax)
sbn.lineplot(x=np.arange(7.8, 12.4, 0.2), y=[cubic_fit_b.params[3]*x*x*x + cubic_fit_b.params[2]*x*x + cubic_fit_b.params[1]*x + cubic_fit_b.params[0] for x in np.arange(7.8, 12.4, 0.2)], color='#322300', ax=ax)

# compare the function from which the data were generated
#
sbn.lineplot(x=np.arange(5.8, 14.4, 0.1), y=[fct_a(x) for x in np.arange(5.8, 14.4, 0.1)], color='#e6503c', ax=ax)
sbn.lineplot(x=np.arange(5.8, 14.4, 0.1), y=[fct_b(x) for x in np.arange(5.8, 14.4, 0.1)], color='#147864', ax=ax)

ax.set(xlim=(6, 14))
ax.set(ylim=(0, 20000))

In [ ]:
# validation data sets (5 points)
#
x_val_dataset = [random.uniform(7, 13) for i in range(5)]
y_val_dataset_a = noisy_function(fct_a, x_val_dataset, 2, 2000)
y_val_dataset_b = noisy_function(fct_b, x_val_dataset, 2, 2000)
print("\n*** VALIDATION DATA ***\n\nx_val_dataset:\t", x_val_dataset)
print("y_val_dataset_a:\t", y_val_dataset_a)
print("y_val_dataset_b:\t", y_val_dataset_b)

# test data sets (5 points)
#
x_test_dataset = [random.uniform(7, 13) for i in range(5)]
y_test_dataset_a = noisy_function(fct_a, x_test_dataset, 2, 2000)
y_test_dataset_b = noisy_function(fct_b, x_test_dataset, 2, 2000)
print("\n*** TEST DATA ***\n\nx_test_dataset:\t", x_test_dataset)
print("y_test_dataset_a:\t", y_test_dataset_a)
print("y_test_dataset_b:\t", y_test_dataset_b)

In [ ]:
# for validation and testing, determine the root mean square deviation between
# data estimated using a correlation expression and the actual data
#
def root_mean_square_deviation(xdata, ydata, estimator, coeff):
    ydata_estimated = [estimator(coeff, x) for x in xdata]
    square_deviation = [(ydata[i] - ydata_estimated[i])**2 for i in range(len(ydata))]
    mean_square_deviation = sum(square_deviation) / len(square_deviation)
    return mean_square_deviation**0.5

# null hypothesis, data are merely fluctuating around a constant value; averages determined above
#
def const_estimator(coeff, x):
    return coeff[0]
const_coeff_list_a = [y_dataset_average_a]
const_coeff_list_b = [y_dataset_average_b]

# linear correlation, parameters determined above
#
def linear_estimator(coeff, x):
    return coeff[0] + x*coeff[1]
linear_coeff_list_a = linear_fit_a.params
linear_coeff_list_b = linear_fit_b.params

# bilogarithmic correlation, parameters determined above
#
def bilog_estimator(coeff, x):
    return math.exp(coeff[0] + math.log(x)*coeff[1])
bilog_coeff_list_a = log_fit_a.params
bilog_coeff_list_b = log_fit_b.params

# cubic correlation, parameters determined above
#
def cubic_estimator(coeff, x):
    return coeff[0] + x*coeff[1] + x*x*coeff[2] + x*x*x*coeff[3]
cubic_coeff_list_a = cubic_fit_a.params
cubic_coeff_list_b = cubic_fit_b.params

In [ ]:
print("*** VALIDATION OF MODELS FOR DATA SET A ***\n")
print("Root mean square deviation from null hypothesis/const.:\t", \
     round(root_mean_square_deviation(x_val_dataset, y_val_dataset_a, const_estimator, const_coeff_list_a), 1))
print("Root mean square deviation from linear regression:\t", \
     round(root_mean_square_deviation(x_val_dataset, y_val_dataset_a, linear_estimator, linear_coeff_list_a), 1))
print("Root mean square deviation from bilog. regression:\t", \
     round(root_mean_square_deviation(x_val_dataset, y_val_dataset_a, bilog_estimator, bilog_coeff_list_a), 1))
print("Root mean square deviation from cubic regression:\t", \
     round(root_mean_square_deviation(x_val_dataset, y_val_dataset_a, cubic_estimator, cubic_coeff_list_a), 1))

In [ ]:
print("*** TEST OF THE FINAL LINEAR REGRESSION MODEL FOR DATA SET A ***\n")
rmsd_a = root_mean_square_deviation(x_test_dataset, y_test_dataset_a, linear_estimator, linear_coeff_list_a)
print("Root mean square deviation from the linear regression:\t", round(rmsd_a, 1))
print("Double root mean square deviation for the margin of error:\t+-", round(2*rmsd_a, 1))

In [ ]:
print("*** VALIDATION OF MODELS FOR DATA SET B ***\n")
print("Root mean square deviation from null hypothesis/const.:\t", \
     round(root_mean_square_deviation(x_val_dataset, y_val_dataset_b, const_estimator, const_coeff_list_b), 1))
print("Root mean square deviation from linear regression:\t", \
     round(root_mean_square_deviation(x_val_dataset, y_val_dataset_b, linear_estimator, linear_coeff_list_b), 1))
print("Root mean square deviation from bilog. regression:\t", \
     round(root_mean_square_deviation(x_val_dataset, y_val_dataset_b, bilog_estimator, bilog_coeff_list_b), 1))
print("Root mean square deviation from cubic regression:\t", \
     round(root_mean_square_deviation(x_val_dataset, y_val_dataset_b, cubic_estimator, cubic_coeff_list_b), 1))

In [ ]:
print("*** TEST OF THE FINAL MODEL (CONSTANT AVERAGE VALUE) FOR DATA SET B ***\n")
rmsd_b = root_mean_square_deviation(x_test_dataset, y_test_dataset_b, const_estimator, const_coeff_list_b)
print("Root mean square deviation from the final constant-value model:\t", round(rmsd_b, 1))
print("Double root mean square deviation for the margin of error:\t+-", round(2*rmsd_b, 1))

In [ ]:
import seaborn as sbn
import matplotlib.pyplot as plt

fig, ax = plt.subplots()
fig.set_size_inches(13, 8)
plt.xticks(fontsize=18, color="#322300")
plt.yticks(fontsize=18, color="#322300")
ax.set_xlabel("x", fontsize=24, color="#322300")
ax.set_ylabel("y", fontsize=24, color="#322300")


sbn.scatterplot(x=x_dataset, y=y_dataset_a, color="#707070", s=50)  # grey for training data set A
sbn.scatterplot(x=x_val_dataset, y=y_val_dataset_a, color="#e6503c", s=90)  # red for validation data set A

plotrange_a = np.arange(5.5, 15.55, 0.1)
plotrange_a_cubic = np.arange(6.5, 13.05, 0.1)
sbn.lineplot(x=plotrange_a, y=[const_estimator(const_coeff_list_a, x) for x in plotrange_a], \
             color='#322300', ax=ax)  # black for constant average value
sbn.lineplot(x=plotrange_a, y=[linear_estimator(linear_coeff_list_a, x) for x in plotrange_a], \
             color='#e6503c', ax=ax)  # red for linear regression
sbn.lineplot(x=plotrange_a, y=[bilog_estimator(bilog_coeff_list_a, x) for x in plotrange_a], \
             color='#002855', ax=ax)  # dark blue for bilogarithmic regression
sbn.lineplot(x=plotrange_a_cubic, y=[cubic_estimator(cubic_coeff_list_a, x) for x in plotrange_a_cubic], \
             color='#00a0d2', ax=ax)  # light blue for cubic regression

ax.set(xlim=(6, 14))
ax.set(ylim=(0, 20000))

In [ ]:
import seaborn as sbn
import matplotlib.pyplot as plt

fig, ax = plt.subplots()
fig.set_size_inches(13, 8)
plt.xticks(fontsize=18, color="#322300")
plt.yticks(fontsize=18, color="#322300")
ax.set_xlabel("x", fontsize=24, color="#322300")
ax.set_ylabel("y", fontsize=24, color="#322300")


sbn.scatterplot(x=x_dataset, y=y_dataset_a, color="#606060", s=40)  # grey for training data set A
sbn.scatterplot(x=x_val_dataset, y=y_val_dataset_a, color="#e6503c", s=80)  # red for validation data set A
sbn.scatterplot(x=x_test_dataset, y=y_test_dataset_a, color="#00a0d2", s=120)  # blue for test data set A

plotrange_a = np.arange(5.5, 15.55, 0.1)
sbn.lineplot(x=plotrange_a, y=[linear_estimator(linear_coeff_list_a, x) for x in plotrange_a], \
             color='#e6503c', ax=ax)  # red for linear regression
sbn.lineplot(x=plotrange_a, y=[linear_estimator(linear_coeff_list_a, x) - 2*rmsd_a for x in plotrange_a], \
             color='#322300', ax=ax)  # black for confidence interval
sbn.lineplot(x=plotrange_a, y=[linear_estimator(linear_coeff_list_a, x) + 2*rmsd_a for x in plotrange_a], \
             color='#322300', ax=ax)  # black for confidence interval

ax.set(xlim=(6, 14))
ax.set(ylim=(0, 20000))

In [ ]:
import seaborn as sbn
import matplotlib.pyplot as plt

fig, ax = plt.subplots()
fig.set_size_inches(13, 8)
plt.xticks(fontsize=18, color="#322300")
plt.yticks(fontsize=18, color="#322300")
ax.set_xlabel("x", fontsize=24, color="#322300")
ax.set_ylabel("y", fontsize=24, color="#322300")


sbn.scatterplot(x=x_dataset, y=y_dataset_b, color="#707070", s=50)  # grey for training data set B
sbn.scatterplot(x=x_val_dataset, y=y_val_dataset_b, color="#147864", s=90)  # green for validation data set B

plotrange_b = np.arange(5.5, 15.55, 0.1)
plotrange_b_cubic = np.arange(7, 15.05, 0.1)
sbn.lineplot(x=plotrange_b, y=[const_estimator(const_coeff_list_b, x) for x in plotrange_b], \
             color='#147864', ax=ax)  # green for constant average value
sbn.lineplot(x=plotrange_b, y=[linear_estimator(linear_coeff_list_b, x) for x in plotrange_b], \
             color='#002855', ax=ax)  # dark blue for linear regression
sbn.lineplot(x=plotrange_b, y=[bilog_estimator(bilog_coeff_list_b, x) for x in plotrange_b], \
             color='#ea7500', ax=ax)  # orange for bilogarithmic regression
sbn.lineplot(x=plotrange_b_cubic, y=[cubic_estimator(cubic_coeff_list_b, x) for x in plotrange_b_cubic], \
             color='#00a0d2', ax=ax)  # light blue for bilogarithmic regression

ax.set(xlim=(6, 14))
ax.set(ylim=(0, 20000))

In [ ]:
import seaborn as sbn
import matplotlib.pyplot as plt

fig, ax = plt.subplots()
fig.set_size_inches(13, 8)
plt.xticks(fontsize=18, color="#322300")
plt.yticks(fontsize=18, color="#322300")
ax.set_xlabel("x", fontsize=24, color="#322300")
ax.set_ylabel("y", fontsize=24, color="#322300")

sbn.scatterplot(x=x_dataset, y=y_dataset_b, color="#606060", s=40)  # grey for training data set B
sbn.scatterplot(x=x_val_dataset, y=y_val_dataset_b, color="#147864", s=80)  # green for validation data set B
sbn.scatterplot(x=x_test_dataset, y=y_test_dataset_b, color="#00a0d2", s=120)  # blue for test data set B

plotrange_b = np.arange(6.5, 13.05, 0.1)
sbn.lineplot(x=plotrange_b, y=[const_estimator(const_coeff_list_b, x) for x in plotrange_b], \
             color='#147864', ax=ax)  # green for constant average value
sbn.lineplot(x=plotrange_b, y=[const_estimator(const_coeff_list_b, x) - 2*rmsd_b for x in plotrange_b], \
             color='#322300', ax=ax)  # black for confidence interval
sbn.lineplot(x=plotrange_b, y=[const_estimator(const_coeff_list_b, x) + 2*rmsd_b for x in plotrange_b], \
             color='#322300', ax=ax)  # black for confidence interval

ax.set(xlim=(6, 14))
ax.set(ylim=(0, 20000))